In [30]:
import stim
from typing import Tuple, Set, Dict, List
from numpy.typing import NDArray
import numpy as np
import sys
import BBcodeinj as BBcode
import pymatching
import matplotlib.pyplot as plt
from itertools import product
import pandas as pd
import seaborn as sns
import cnotsynthesis as cs
import testinverse as ts
import findlogicalbasis

In [32]:
def bb_injection(rounds: int, noise_profile: list[float], inject_state: str) -> stim.Circuit:
    
    p1, p2, p_M, p_R = noise_profile

    A=[[3, 0], [0, 1], [0, 2]]
    B=[[0, 3], [1, 0], [2, 0]]
    l=12
    m=6

    bb_code = BBcode.BBcode(n=144, k=12, d=12, m = m,l = l,
                             A = A,
                             B = B,
                             shift=[0, 0],
                             f=[[0, 0], [1, 0], [2, 0], [3, 0], [6, 0], [7, 0], [8, 0], [9, 0], [1, 3], [5, 3], [7, 3], [11, 3]],
                             g=[[1, 0], [2, 1], [0, 2], [1, 2], [2, 3], [0, 4]],
                             h=[[0, 0], [0, 1], [1, 1], [0, 2], [1, 3], [0, 3]],
                             alpha=[[0, 0], [0, 1], [2, 1], [2, 5], [3, 2], [4, 0]],
                             beta =[[0, 1], [0, 5], [1, 1], [0, 0], [4, 0], [5, 2]])

    full_circuit = stim.Circuit()

    X_matrix  = np.array([[0,0,0,0,0,0,0,0,0,1,1,1],
        [0,0,0,0,0,0,0,0,0,0,1,1],
        [0,0,1,1,0,0,1,1,1,0,1,1],
        [0,0,0,1,0,1,0,0,0,0,0,0],
        [0,0,0,0,0,0,0,0,0,0,1,0],
        [0,0,1,0,0,1,1,1,0,0,0,1],
        [0,0,0,0,1,1,1,1,0,0,0,0],
        [1,0,0,0,1,1,0,1,0,0,0,0],
        [1,0,0,0,1,1,0,0,0,0,0,0],
        [0,1,0,0,1,1,1,1,0,0,0,0],
        [1,1,0,0,0,1,0,1,0,0,0,0],
        [0,0,0,0,0,0,1,0,0,0,0,0]], dtype=np.uint8)

    Z_matrix = np.array([[0,0,0,0,0,0,0,0,0,1,0,0],
        [0,0,1,0,0,0,0,0,0,1,0,1],
        [0,0,0,0,0,0,0,0,1,0,0,0],
        [0,0,0,1,0,0,0,0,1,0,0,0],
        [0,0,1,0,0,0,0,0,1,0,1,1],
        [0,0,1,0,0,0,0,0,1,0,0,0],
        [1,1,0,0,1,0,0,0,0,0,0,0],
        [1,0,1,0,1,0,0,1,0,0,0,0],
        [0,0,0,1,0,1,0,1,0,0,0,0],
        [0,1,1,1,1,1,0,0,0,0,0,0],
        [0,0,1,1,1,1,0,0,0,0,0,0],
        [1,0,0,1,0,1,1,0,0,0,0,0]], dtype=np.uint8)

    
    inject_qubit_raw = [130, 131, 132, 133, 134, 135, 136, 137, 140, 141, 142, 143]
    measure_X_raw = [76, 77, 62, 63, 64, 65, 82, 83, 68, 69, 70, 71, 88, 84, 85, 86, 87, 138, 94, 90, 91, 92, 93, 126, 100, 96, 80, 81, 98, 99, 89, 102, 103, 104, 105, 139, 95, 108, 109, 110, 111, 127, 101, 97, 114, 115, 116, 117, 106, 107, 120, 122, 123, 121, 57, 58, 59, 113, 112, 56, 118, 119, 128, 129, 124, 125]
    measure_Z_raw = [1, 2, 3, 4, 0, 18, 7, 8, 9, 10, 6, 24, 13, 14, 15, 16, 12, 30, 19, 20, 21, 22, 36, 37, 25, 26, 27, 28, 42, 43, 31, 32, 33, 34, 48, 49, 38, 41, 39, 40, 54, 55, 44, 47, 45, 46, 60, 61, 50, 53, 51, 52, 66, 67, 5, 23, 72, 74, 75, 73, 11, 29, 78, 79, 17, 35]
    inject_qubit = ts.convert_index(inject_qubit_raw)
    measure_X = ts.convert_index(measure_X_raw)
    measure_Z = ts.convert_index(measure_Z_raw)

    coord_to_index = bb_code.coord_to_index
    data_coords = bb_code.data_coords
    ancilla_coords = bb_code.ancilla_coords
    ancilla_coords_z = bb_code.ancilla_coords_z
    ancilla_coords_x = bb_code.ancilla_coords_x

    # Add QUBIT_COORDS annotations
    for (x, y), index in coord_to_index.items():
        full_circuit.append('QUBIT_COORDS', [index], [x, y])

    # Initialization pattern
    X_data = []
    Z_data = []
    inject_data = []

    for x,y in data_coords:
        if x % 2 == 0 and ((x // 2)+ 12*( y//2 ) in measure_X):
            X_data.append((x, y))
        elif x % 2 == 1 and ( ((x // 2)+ 12*( y//2 ) + 72) in measure_X):
            X_data.append((x, y))
        elif x % 2 == 0 and ((x // 2)+ 12*( y//2 ) in measure_Z):
            Z_data.append((x, y))
        elif x % 2 == 1 and ( ((x // 2)+ 12*( y//2 ) + 72) in measure_Z):
            Z_data.append((x, y))
    
    for k in inject_qubit:
        if k >=72:
            y = (k - 72) // 12
            x = (k - 72) % 12
            inject_data.append((2*x+1,2*y))
        else:
            y = k // 12
            x = k % 12
            inject_data.append((2*x,2*y+1))
        

    X_indices = [coord_to_index[q] for q in X_data]
    Z_indices = [coord_to_index[q] for q in Z_data]
    inject_indices= [coord_to_index[q] for q in inject_data]

    full_circuit.append_operation("RX", X_indices)
    full_circuit.append_operation("Z_ERROR", X_indices, p_R)
    full_circuit.append_operation("R", Z_indices)
    full_circuit.append_operation("X_ERROR", Z_indices, p_R)

    # Injected simulatable state into qubits (|0> or |+>)
    if inject_state == "Z":
        full_circuit.append_operation("R", inject_indices)
        full_circuit.append_operation("X_ERROR", inject_indices, p_R)
    elif inject_state == "X":
        full_circuit.append_operation("RX", inject_indices)
        full_circuit.append_operation("Z_ERROR", inject_indices, p_R)
    else:
        raise ValueError("inject_state must be 'Z' or 'X'")
    full_circuit.append("TICK")

    # Clifford gates to prepare the initial state
    ops=ts.find_reversal_circuit(X_matrix)
    pairs = cs.map_ops_to_physical(ops, inject_indices)

    for a,b in pairs:
        full_circuit.append_operation("CNOT", [a, b])
        full_circuit.append_operation("DEPOLARIZE2", [a,b], p2)
    full_circuit.append("TICK")


    # First round of SM
    one_round = bb_code.build_standard_sm_round(noise_profile)
    full_circuit += one_round

    #Compute fisrt round detectors
    def testfirstroundancilla(anc,measure_X_raw,measure_Z_raw,l,m):
        check = False
        x,y = anc
        if x % 2 == 0:
            x = x // 2
            y = y // 2
            listqubits = []
            for i in range(3):  
                listqubits.append(6*(x + A[i][0] % l)+((y+ A[i][1]) % m))
                listqubits.append(72 + 6*(x + B[i][0] % l)+((y+ B[i][1]) % m))
                check = all(elem in measure_X_raw for elem in listqubits)
        elif x % 2 == 1:
            x = x // 2
            y = y // 2
            listqubits = []
            for i in range(3):  
                listqubits.append(72 + 6*(x - A[i][0] % l)+((y - A[i][1]) % m))
                listqubits.append(6*(x + B[i][0] % l)+((y+ B[i][1]) % m))
                check = all(elem in measure_Z_raw for elem in listqubits)
        return check

    #First round detectors are those stabilizers formed by the initialization
    for k, anc in enumerate(ancilla_coords):
        if anc in ancilla_coords_x:
            check = testfirstroundancilla(anc,measure_X_raw,measure_Z_raw,l,m)
            if check:
                full_circuit.append_operation("DETECTOR", [stim.target_rec(-k - 1)], list(anc) + [0])
        elif anc in ancilla_coords_z:
            check = testfirstroundancilla(anc,measure_Z_raw,measure_Z_raw,l,m)
            if check:
                full_circuit.append_operation("DETECTOR", [stim.target_rec(-k - 1)], list(anc) + [0])

    # Later rounds
    repeat_circuit = stim.Circuit()
    repeat_circuit.append("TICK")
    repeat_circuit += bb_code.build_standard_sm_round(noise_profile)
    repeat_circuit.append_operation("SHIFT_COORDS", [], [0,0,1])

    # Insert detectors
    for k, ancilla in enumerate(reversed(ancilla_coords)):
        prev = -k - 1 - len(ancilla_coords)
        repeat_circuit.append_operation("DETECTOR", [stim.target_rec(-k - 1), stim.target_rec(prev)], list(ancilla) + [0])
    full_circuit += repeat_circuit * (rounds-1)

    # Final data measurement
    final_measure_indices = [coord_to_index[c] for c in data_coords]
    if inject_state == "X":
        full_circuit.append_operation("H", final_measure_indices)
        # We don't insert errors because measuring data qubits is not included in the injection protocol,
        # but just used to infer the logical operator; there will be no new detectors
    full_circuit.append_operation("M", final_measure_indices)

    # Logical observable, depending on the inject state
    logical_operators = getattr(bb_code, 'logical_' + inject_state)
    for i, logical_operator in enumerate(logical_operators):
        obs_targets = [stim.target_rec(-data_coords[::-1].index(c) - 1) for c in logical_operator]
        full_circuit.append("OBSERVABLE_INCLUDE", obs_targets, i)
    

    return full_circuit

In [33]:
bb_code = BBcode.BBcode(n=144, k=12, d=12, m=6, l=12,
                             A=[[3, 0], [0, 1], [0, 2]],
                             B=[[0, 3], [1, 0], [2, 0]],
                             shift=[0, 0],
                             f=[[0, 0], [1, 0], [2, 0], [3, 0], [6, 0], [7, 0], [8, 0], [9, 0], [1, 3], [5, 3], [7, 3], [11, 3]],
                             g=[[1, 0], [2, 1], [0, 2], [1, 2], [2, 3], [0, 4]],
                             h=[[0, 0], [0, 1], [1, 1], [0, 2], [1, 3], [0, 3]],
                             alpha=[[0, 0], [0, 1], [2, 1], [2, 5], [3, 2], [4, 0]],
                             beta =[[0, 1], [0, 5], [1, 1], [0, 0], [4, 0], [5, 2]])
logical_operators = getattr(bb_code, 'logical_Z')

In [34]:
rounds = 3
noise_profile = [1e-3, 1e-3, 1e-3, 1e-3]
corner_inject_Z = bb_injection(rounds, noise_profile, "Z")
corner_inject_X = bb_injection(rounds, noise_profile, "X")
corner_inject_Z.without_noise().diagram("detslice-with-ops-svg",filter_coords=['L1'])

In [35]:
corner_inject_X

stim.Circuit('''
    QUBIT_COORDS(0, 0) 0
    QUBIT_COORDS(1, 0) 1
    QUBIT_COORDS(2, 0) 2
    QUBIT_COORDS(3, 0) 3
    QUBIT_COORDS(4, 0) 4
    QUBIT_COORDS(5, 0) 5
    QUBIT_COORDS(6, 0) 6
    QUBIT_COORDS(7, 0) 7
    QUBIT_COORDS(8, 0) 8
    QUBIT_COORDS(9, 0) 9
    QUBIT_COORDS(10, 0) 10
    QUBIT_COORDS(11, 0) 11
    QUBIT_COORDS(12, 0) 12
    QUBIT_COORDS(13, 0) 13
    QUBIT_COORDS(14, 0) 14
    QUBIT_COORDS(15, 0) 15
    QUBIT_COORDS(16, 0) 16
    QUBIT_COORDS(17, 0) 17
    QUBIT_COORDS(18, 0) 18
    QUBIT_COORDS(19, 0) 19
    QUBIT_COORDS(20, 0) 20
    QUBIT_COORDS(21, 0) 21
    QUBIT_COORDS(22, 0) 22
    QUBIT_COORDS(23, 0) 23
    QUBIT_COORDS(0, 1) 24
    QUBIT_COORDS(1, 1) 25
    QUBIT_COORDS(2, 1) 26
    QUBIT_COORDS(3, 1) 27
    QUBIT_COORDS(4, 1) 28
    QUBIT_COORDS(5, 1) 29
    QUBIT_COORDS(6, 1) 30
    QUBIT_COORDS(7, 1) 31
    QUBIT_COORDS(8, 1) 32
    QUBIT_COORDS(9, 1) 33
    QUBIT_COORDS(10, 1) 34
    QUBIT_COORDS(11, 1) 35
    QUBIT_COORDS(12, 1) 36
    QUBIT_COOR

In [36]:
num_shots = 1000000
samples_Z = corner_inject_Z.compile_detector_sampler().sample(num_shots, append_observables=True)

In [ ]:
def LER_postselect(samples: NDArray[np.bool_],num_observables) -> list[float]:
    # Assume one observable at the end
    postselected = [s for s in samples if sum(s[:-num_observables]) == 0]
    N = len(postselected)
    n = sum(s[-num_observables:] for s in postselected)

    # Logical error rate with postselection
    if N > 0:
        ler_post = n / N

    # Logical error rate without post-selection
    n_total = len(samples)
    n_obs = sum(s[-num_observables:] for s in samples)
    ler_no_post = n_obs / n_total

    postselected_rate = N/n_total
    
    return ler_post, ler_no_post, postselected_rate

def LER_postselectsingle(samples: NDArray[np.bool_],num_observables) -> list[float]:
    # Assume one observable at the end
    postselected = [s for s in samples if sum(s[:-1]) == 0]
    N = len(postselected)
    n = sum(s[-1:] for s in postselected)

    # Logical error rate with postselection
    if N > 0:
        ler_post = n / N

    # Logical error rate without post-selection
    n_total = len(samples)
    n_obs = sum(s[-1:] for s in samples)
    ler_no_post = n_obs / n_total

    postselected_rate = N/n_total
    
    return ler_post, ler_no_post, postselected_rate

In [42]:
num_shots = 1000000
single = True
num_observables = bb_code.k
samples_Z = corner_inject_Z.compile_detector_sampler().sample(num_shots, append_observables=True)
print("Inject state: Z")
if single:
    LER_post, LER_no_post, postselected_rate = LER_postselectsingle(samples_Z,num_observables)
else:
    LER_post, LER_no_post, postselected_rate = LER_postselect(samples_Z,num_observables)
print(f"LER_post: {LER_post}, LER_no_post: {LER_no_post}, Post-selection Rate: {postselected_rate}")
samples_X = corner_inject_X.compile_detector_sampler().sample(num_shots, append_observables=True)
print("Inject state: X")
if single:
    LER_post, LER_no_post, postselected_rate = LER_postselectsingle(samples_X,num_observables)
else:
    LER_post, LER_no_post, postselected_rate = LER_postselect(samples_X,num_observables)
print(f"LER_post: {LER_post}, LER_no_post: {LER_no_post}, Post-selection Rate: {postselected_rate}")

Inject state: Z
LER_post: [0.00014385 0.00110285], LER_no_post: [0.364753 0.376206], Post-selection Rate: 0.020855
Inject state: X
LER_post: [0.00353554 0.00558243], LER_no_post: [0.378282 0.331596], Post-selection Rate: 0.021496
